In [0]:
%run ./conf_notebook

Import the data

In [0]:
df_train = ps.read_csv(train_1_csv_file_path)
df_train = df_train.drop('_c0', axis=1)

path name size modificationTime dbfs:/mnt/pqsashrd/data/ann_pred_1.csv/ ann_pred_1.csv/ 0 0 dbfs:/mnt/pqsashrd/data/ann_pred_1_test.csv/ ann_pred_1_test.csv/ 0 0 dbfs:/mnt/pqsashrd/data/ann_pred_3.csv/ ann_pred_3.csv/ 0 0 dbfs:/mnt/pqsashrd/data/clust_pred_1.csv/ clust_pred_1.csv/ 0 0 dbfs:/mnt/pqsashrd/data/clust_pred_1_test.csv/ clust_pred_1_test.csv/ 0 0 dbfs:/mnt/pqsashrd/data/clust_pred_3.csv/ clust_pred_3.csv/ 0 0 dbfs:/mnt/pqsashrd/data/clust_pred_3_test.csv/ clust_pred_3_test.csv/ 0 0 dbfs:/mnt/pqsashrd/data/test_1.csv test_1.csv 38574669 1714569841000 dbfs:/mnt/pqsashrd/data/test_2.csv test_2.csv 35056701 1714569835000 dbfs:/mnt/pqsashrd/data/test_3.csv test_3.csv 25575183 1714569796000 dbfs:/mnt/pqsashrd/data/train_1.csv train_1.csv 81417863 1714569888000 dbfs:/mnt/pqsashrd/data/train_1_partitioned/ train_1_partitioned/ 0 0 dbfs:/mnt/pqsashrd/data/train_2.csv train_2.csv 73764410 1714569886000 dbfs:/mnt/pqsashrd/data/train_3.csv train_3.csv 54130409 1714569868000 dbfs:/mnt/pqsashrd/data/train_3_partitioned/ train_3_partitioned/ 0 0

In [0]:
label_encoder = LabelEncoder()
df_train = df_train.to_pandas()
df_train["attack_cat_encoded"] = label_encoder.fit_transform(df_train["attack_cat"])
df_train = ps.DataFrame(df_train)

In [0]:
X_train = df_train.set_index("attack_cat")
X_train = X_train.drop("attack_cat_encoded", axis=1)
y_train = df_train["attack_cat_encoded"]

Adjusted Rand Index (ARI): This metric measures the similarity between two clusterings by considering all pairs of samples and counting pairs that are assigned in the same or different clusters in the predicted and true clusterings. The ARI is adjusted for chance, which makes it more robust for comparing different clustering algorithms.

Silhouette Coefficient: This metric measures how similar an object is to its own cluster (cohesion) compared to other clusters (separation). The Silhouette Coefficient is calculated for each sample and can range from -1 to +1, where a high value indicates that the object is well matched to its own cluster and poorly matched to neighboring clusters. If most objects have a high value, the clustering configuration is appropriate.

### Fuzzy K-MEANS 

In [0]:
estimator = LDA(n_components = 2)
X_lda = estimator.fit_transform(ps.DataFrame(X_train).to_pandas(), y_train.to_pandas())
X_lda_df = ps.DataFrame(data=X_lda, columns=['LDA_component_1', 'LDA_component_2'], index=ps.DataFrame(X_train).index)
X_lda_df = X_lda_df.to_pandas()

In [0]:
custom_color_scale = [
    '#800080',  # Purple (no change)
    '#9370db',  # Medium Purple (no change)
    '#6495ed',  # Cornflower Blue (no change)
    '#000080',  # Navy (no change)
    '#6998b3',  # Darker Light Blue (no change)
    "#e4cbd1",  # Medium Violet Red (a darker, more subdued pink)
]

In [0]:
estimator = LDA(n_components = 4)
X_lda = estimator.fit_transform(X_train.to_pandas(), y_train.to_pandas())
X_lda_df_ = ps.DataFrame(data=X_lda, columns=['LDA_component_1', 'LDA_component_2', 'LDA_component_3', 'LDA_component_4'], index=X_train.index)
X_lda_df_ = X_lda_df_.to_pandas()
true_labels = y_train.to_numpy()

In [0]:
silhouette_scores = []
aris = []

for k in range(2,11): 
    cntr, u, u0, d, jm, p, fpc = fuzz.cluster.cmeans(X_lda_df_.T, c=k, m=5, error=0.00001, maxiter=100000)
    predicted_labels = np.argmax(u, axis=0)

    ari = metrics.adjusted_rand_score(true_labels, predicted_labels)

    spark_df = spark.createDataFrame([(Vectors.dense(x), int(l)) for x, l in zip(X_lda_df_.values, predicted_labels)], ["features", "prediction"])
    evaluator = ClusteringEvaluator(predictionCol='prediction', featuresCol='features', metricName='silhouette', distanceMeasure='squaredEuclidean')
    silhouette_score = evaluator.evaluate(spark_df)

    print(f"Number of clusters = {k}: Silhouette Coefficient = {silhouette_score}, Adjusted Rand Index (ARI) = {ari}")
    silhouette_scores.append(silhouette_score)
    aris.append(ari)

Number of clusters = 2: Silhouette Coefficient = 0.7201799633469588, Adjusted Rand Index (ARI) = 0.23645454027021112
Number of clusters = 3: Silhouette Coefficient = 0.7169248177924304, Adjusted Rand Index (ARI) = 0.4148163708794586
Number of clusters = 4: Silhouette Coefficient = 0.7558060792608947, Adjusted Rand Index (ARI) = 0.5386119815651794
Number of clusters = 5: Silhouette Coefficient = 0.7683688116933762, Adjusted Rand Index (ARI) = 0.5794686582001407


com.databricks.backend.common.rpc.CommandCancelledException
	at com.databricks.spark.chauffeur.SequenceExecutionState.$anonfun$cancel$3(SequenceExecutionState.scala:103)
	at scala.Option.getOrElse(Option.scala:189)
	at com.databricks.spark.chauffeur.SequenceExecutionState.$anonfun$cancel$2(SequenceExecutionState.scala:103)
	at com.databricks.spark.chauffeur.SequenceExecutionState.$anonfun$cancel$2$adapted(SequenceExecutionState.scala:100)
	at scala.collection.immutable.Range.foreach(Range.scala:158)
	at com.databricks.spark.chauffeur.SequenceExecutionState.cancel(SequenceExecutionState.scala:100)
	at com.databricks.spark.chauffeur.ExecContextState.cancelRunningSequence(ExecContextState.scala:714)
	at com.databricks.spark.chauffeur.ExecContextState.$anonfun$cancel$1(ExecContextState.scala:430)
	at scala.Option.getOrElse(Option.scala:189)
	at com.databricks.spark.chauffeur.ExecContextState.cancel(ExecContextState.scala:430)
	at com.databricks.spark.chauffeur.ChauffeurState.cancelExecutio

In [0]:
k=5
cntr, u, u0, d, jm, p, fpc = fuzz.cluster.cmeans(X_lda_df_.T, c=k, m=2, error=0.00001, maxiter=100000)
predicted_labels = np.argmax(u, axis=0)

ari = metrics.adjusted_rand_score(true_labels, predicted_labels)

spark_df = spark.createDataFrame([(Vectors.dense(x), int(l)) for x, l in zip(X_lda_df_.values, predicted_labels)], ["features", "prediction"])
evaluator = ClusteringEvaluator(predictionCol='prediction', featuresCol='features', metricName='silhouette', distanceMeasure='squaredEuclidean')
silhouette_score = evaluator.evaluate(spark_df)

print(f"Number of clusters = {k}: Silhouette Coefficient = {silhouette_score}, Adjusted Rand Index (ARI) = {ari}")

Number of clusters = 5: Silhouette Coefficient = 0.8679087920124233, Adjusted Rand Index (ARI) = 0.5703486331040698


In [0]:
num_clusters = [2, 3, 4, 5, 6, 7, 8, 9, 10, 8]  
silhouette_scores = silhouette_scores 
ari_scores = aris

blue1 = 'rgb(0, 123, 255)'  
blue2 = 'rgb(0, 0, 139)'

trace1 = go.Scatter(
    x=num_clusters,
    y=silhouette_scores,
    mode='lines+markers',
    name='Silhouette Score',
    line=dict(color=blue1),
    marker=dict(color=blue1)
)

trace2 = go.Scatter(
    x=num_clusters,
    y=ari_scores,
    mode='lines+markers',
    name='ARI Score',
    line=dict(color=blue2),
    marker=dict(color=blue2)
)

data = [trace1, trace2]

layout = dict(title='Silhouette Score and ARI vs Number of Clusters',
              xaxis=dict(title='Number of Clusters'),
              yaxis=dict(title='Score'),
              )

fig = dict(data=data, layout=layout)
iplot(fig)

In [0]:
k=5
cntr, u, u0, d, jm, p, fpc = fuzz.cluster.cmeans(X_lda_df_.T, c=k, m=2, error=0.00001, maxiter=100000)
predicted_labels = np.argmax(u, axis=0)
# u membership function: verctors sum 1:)

ari = metrics.adjusted_rand_score(true_labels, predicted_labels)

spark_df = spark.createDataFrame([(Vectors.dense(x), int(l)) for x, l in zip(X_lda_df_.values, predicted_labels)], ["features", "prediction"])
evaluator = ClusteringEvaluator(predictionCol='prediction', featuresCol='features', metricName='silhouette', distanceMeasure='squaredEuclidean')
silhouette_score = evaluator.evaluate(spark_df)

print(f"Number of clusters = {k}: Silhouette Coefficient = {silhouette_score}, Adjusted Rand Index (ARI) = {ari}")

Number of clusters = 5: Silhouette Coefficient = 0.8679087920124233, Adjusted Rand Index (ARI) = 0.5703486331040698


In [0]:
X_lda_df["pred"] = predicted_labels

fig = px.scatter(X_lda_df, x='LDA_component_1', y='LDA_component_2', color=X_lda_df["pred"], color_continuous_scale=custom_color_scale)
fig.update_layout(
    title='LDA Scatter Plot in 2D',
    scene = dict(
        xaxis_title='LDA Component 1',
        yaxis_title='LDA Component 2',
    ),
    legend_title='Attack category',
    width=800,
    height=600
)
fig.show()